# Web scrapping stock prices
This code accesses site to retrieve stock price information and then saves it to an individual csv file for each stock.

This code is for 10 YEAR STOCK HISTORY

The sources of data are:
- https://en.wikipedia.org/wiki/FTSE_100_Index -> list of FTSE 100 company stock tickers
- https://en.wikipedia.org/wiki/FTSE_250_Index -> list of FTSE 250 company stock tickers
- https://finance.yahoo.com/quote/{stock-ticker}/history?period1={start-time-mark}&period2={end-time-mark}&interval={interval}&filter=history&frequency={frequency} -> Example web address to retrieve information from Yahoo finance
    - Data on this page is scroll loaded so many time indexes must be used toretrieve the dcorrect data
    - Up to 145 records can be seen from initial page load note that this includes dividends so limit to 140 for safety

The inputs required for scrapping are:
 - {stock-ticker} -> this is the ticker taken from wiki with ".L" appended to it
 - {start-tme-mark} -> This is the time in seconds since 01/01/1970 at which you would like the data retrieval to start, data retrieved is inclusive of this time
 - {end-tme-mark} -> This is the time in seconds since 01/01/1970, data retrieved is inclusive of this time
 - {interval} & {frequency} -> This is the interval for which values are given, the two must match
     - 1d = 1 every 1 days
     - 1wk = 1 every week
     - 1mo = 1 eveery month

In [1]:
#Import libraries
import pandas as pd
import numpy as np
from bs4 import BeautifulSoup as bs
import requests as rq
import re
import datetime as dt
import os
import tables
from rf_modules import *

# Delete the old temporary files (if they exist)

In [2]:
#close any open h5 files
tables.file._open_files.close_all()

In [3]:
#Delete the old h5 files
src_fldr_pth = r'C:\\Users\\Robert\\Documents\\python_scripts\\stock_trading_ml_modelling\\historical_prices\\'
try:
    os.remove(src_fldr_pth + r'all_hist_prices_d_TMP.h5')
    print('\nSUCCESSFULLY REMOVED {}'.format(src_fldr_pth + r'all_hist_prices_d_TMP.h5'))
except Exception as e:
    print('\nERROR - REMOVING:{}'.format(e))
try:
    os.remove(src_fldr_pth + r'all_hist_prices_w_TMP.h5')
    print('\nSUCCESSFULLY REMOVED {}'.format(src_fldr_pth + r'all_hist_prices_w_TMP.h5'))
except Exception as e:
    print('\nERROR - REMOVING:{}'.format(e))


ERROR - REMOVING:[WinError 2] The system cannot find the file specified: 'C:\\\\Users\\\\Robert\\\\Documents\\\\python_scripts\\\\stock_trading_ml_modelling\\\\historical_prices\\\\all_hist_prices_d_TMP.h5'

ERROR - REMOVING:[WinError 2] The system cannot find the file specified: 'C:\\\\Users\\\\Robert\\\\Documents\\\\python_scripts\\\\stock_trading_ml_modelling\\\\historical_prices\\\\all_hist_prices_w_TMP.h5'


# Scraping tickers
This section will scrap the ticker values for the FTSE 100 and FTSE 250 and store them in dataframes "tick_ftse100" and "tick_ftse250".

Finally concatenate into 1 dataframe "tick_ftse".

In [4]:
#Fetch the data for ftse 100
web_add = r'https://www.londonstockexchange.com/exchange/prices-and-markets/stocks/indices/summary/summary-indices-constituents.html?index=UKX&page=1'
resp = rq.get(web_add)
parser = bs(resp.content,'html.parser')
#Find how many pages there are to collect
par_elem = parser.find_all('div',id='pi-colonna1-display')[0]
num_pages = int(re.sub('[^0-9]','',par_elem.find_all('p')[0].text[-3:]))

#Collect the rows of data
row_li = []
for page in range(1,num_pages+1):
    web_add = r'https://www.londonstockexchange.com/exchange/prices-and-markets/stocks/indices/summary/summary-indices-constituents.html?index=UKX&page={}'.format(page)
    resp = rq.get(web_add)
    parser = bs(resp.content,'html.parser')
    #Find how many pages there are to collect
    par_elem = parser.find_all('div',id='pi-colonna1-display')[0]
    #Collect the table
    table = par_elem.find_all('table')[0]
    #Collect the rows of data
    for row in table.tbody.find_all('tr'):
        temp_row = []
        for cell in row.find_all('td')[:2]:
            temp_row.append(re.sub('\n','',cell.text.upper()))
        row_li.append(temp_row)
print('count -> {}'.format(len(row_li)))
#Create a dataframe
tick_ftse100 = pd.DataFrame(data=row_li,columns=['ticker','company'])
tick_ftse100['index'] = 'FTSE100'
tick_ftse100.head()

count -> 101


ticker         company    index
0    III         3I GRP.  FTSE100
1    ABF        A.B.FOOD  FTSE100
2    ADM     ADMIRAL GRP  FTSE100
3    AAL  ANGLO AMERICAN  FTSE100
4   ANTO     ANTOFAGASTA  FTSE100

In [5]:
#Fetch the data for ftse 250
web_add = r'https://www.londonstockexchange.com/exchange/prices-and-markets/stocks/indices/summary/summary-indices-constituents.html?index=MCX&page=1'
resp = rq.get(web_add)
parser = bs(resp.content,'html.parser')
#Find how many pages there are to collect
par_elem = parser.find_all('div',id='pi-colonna1-display')[0]
num_pages = int(re.sub('[^0-9]','',par_elem.find_all('p')[0].text[-3:]))

#Collect the rows of data
row_li = []
for page in range(1,num_pages+1):
    web_add = r'https://www.londonstockexchange.com/exchange/prices-and-markets/stocks/indices/summary/summary-indices-constituents.html?index=MCX&page={}'.format(page)
    resp = rq.get(web_add)
    parser = bs(resp.content,'html.parser')
    #Find how many pages there are to collect
    par_elem = parser.find_all('div',id='pi-colonna1-display')[0]
    #Collect the table
    table = par_elem.find_all('table')[0]
    #Collect the rows of data
    for row in table.tbody.find_all('tr'):
        temp_row = []
        for cell in row.find_all('td')[:2]:
            temp_row.append(re.sub('\n','',cell.text.upper()))
        row_li.append(temp_row)
print('count -> {}'.format(len(row_li)))
#Create a dataframe
tick_ftse250 = pd.DataFrame(data=row_li,columns=['ticker','company'])
tick_ftse250['index'] = 'FTSE250'
tick_ftse250.head()

count -> 250


ticker          company    index
0    3IN      3I INF. ORD  FTSE250
1   FOUR    4IMPRINT GRP.  FTSE250
2    ASL  ABERFTH.SMLL.CO  FTSE250
3    AGK          AGGREKO  FTSE250
4    AAF    AIRTEL AFRICA  FTSE250

In [6]:
#Combine into 1 dataframe
tick_ftse = pd.concat([tick_ftse100,tick_ftse250])
tick_ftse

ticker         company    index
0      III         3I GRP.  FTSE100
1      ABF        A.B.FOOD  FTSE100
2      ADM     ADMIRAL GRP  FTSE100
3      AAL  ANGLO AMERICAN  FTSE100
4     ANTO     ANTOFAGASTA  FTSE100
..     ...             ...      ...
245   WTAN   WITAN INV TST  FTSE250
246   WIZZ        WIZZ AIR  FTSE250
247    WG.     WOOD GRP(J)  FTSE250
248    WKP  WORKSPACE GRP.  FTSE250
249    WWH    WORLDWIDE HC  FTSE250

[351 rows x 3 columns]

# Scraping a stock history
Working backwards through time from now until 01/01/1970 collect all the daily data for a stock. Daily is used as it can later be summarised into weekly or monthly if required.

This will then be put into a dataframe containing:
- Ticker
- Company name
- Date
- Open
- High
- Low
- Close
- Adjusted close (for divs and splits)
- Volume

In [7]:
#Create a list of time intervals to be used with 140 days in each item
def create_sec_ref_li(_st_date:int,_en_date:int):
    #Establish the day ref of the dates compared to 01/01/1970
    _ep_date = pd.to_datetime(dt.datetime(1970,1,1),errors='coerce')
    _en_date = pd.to_datetime(_en_date,errors='coerce')
    _st_date = pd.to_datetime(_st_date,errors='coerce')
    print('_st_date: ' + str(_st_date))
    print('_en_date: ' + str(_en_date))
    _st_days = (_st_date - _ep_date).days
    _en_days = (_en_date - _ep_date).days
    #Loop adding to a list until reaching 0
    _sec_ref_li = []
    _days = 140
    while _en_days > _st_days:
        if _en_days - _days > _st_days:
            _sec_ref_li.append([(_en_days - _days)*86400,_en_days*86400])
        else:
            _sec_ref_li.append([_st_days*86400,_en_days*86400])        
        _en_days += -_days
    return _sec_ref_li

In [8]:
def calc_ema(s_in,periods):
    #Calc mod val
    mod = 2/(periods+1)
    #Make a df
    tmp_df = pd.DataFrame(s_in)
    #Calc sma
    tmp_df["sma"] = pd.Series([0] * len(s_in))
    for i in range(0,periods):
        tmp_df["sma"] += tmp_df[s_in.name].shift(i) / periods
    #Calc ema
    tmp_df["ema"] = tmp_df["sma"].copy()
    for row in tmp_df.iterrows():
        i = row[0]
        if i > 0 and not np.isnan(tmp_df["sma"][i-1]):
            tmp_df["ema"][i] = mod*(tmp_df[s_in.name][i] - tmp_df["ema"][i-1]) + tmp_df["ema"][i-1]
    return tmp_df["ema"].copy()

In [9]:
def calc_macd(ema_lng_s,ema_sht_s,sig_period):
    #Make a df
    tmp_df = pd.DataFrame([])
    tmp_df["ema_lng"] = ema_lng_s
    tmp_df["ema_sht"] = ema_sht_s
    #Calc the signal line
    tmp_df["macd_line"] = tmp_df["ema_sht"] - tmp_df["ema_lng"]
    tmp_df["signal_line"] = calc_ema(tmp_df["macd_line"],sig_period)
    tmp_df["macd_hist"] = tmp_df["macd_line"] - tmp_df["signal_line"]
    return (tmp_df["macd_line"].copy(),tmp_df["signal_line"].copy(),tmp_df["macd_hist"].copy())

In [10]:
col_lens = {
     'ticker': 4,
     'date': 19,
     'open': 7,
     'close': 7,
     'high': 7,
     'low': 7,
     'change': 21,
     'volume': 12,
     'ema12': 18,
     'ema26': 18,
     'macd_line': 23,
     'signal_line': 23,
     'macd': 23
}

In [11]:
#Get the price history for a specific ticker
def get_price_hist_d(_tick:str,_sec_ref_li:list):
    try:
        _tick = re.sub('[^A-Z0-9\-]','',_tick)
        print('Getting DAILY prices for:{}'.format(_tick))
        _tick_df = pd.DataFrame([])
        _cols = []

        for _secs in _sec_ref_li:
            try:
                _web_add = 'https://finance.yahoo.com/quote/{0}/history?period1={1}&period2={2}&interval={3}&filter=history&frequency={3}'.format(_tick+'.L',_secs[0],_secs[1],'1d')
#                 print('_web_add: {}'.format(_web_add))
                _resp = rq.get(_web_add)
                if int(_resp.status_code) != 200:
                    print('status code: {}'.format(_resp.status_code))
                    continue
                _parser = bs(_resp.content,'html.parser')
                #Get the table
                _table = _parser.find_all('table',attrs={'data-test':'historical-prices'})[0]
                #Grab the data rows
                _rows = _table.find_all('tbody')[0].find_all('tr')
                #Put the rows into the dataframe
                for _r in _rows:
                    if _tick_df.shape[0] == 0:
                        _cols = [clean_col_name(x.text) for x in _table.find_all('th')]
                        _tick_df = pd.DataFrame([],columns=_cols)
                    if len(_r.find_all('td')) == len(_cols):
                        _tick_df = _tick_df.append(pd.Series([x.text for x in _r.find_all('td')],index=_cols),ignore_index=True)
                    else:
                        continue
            except Exception as e:
                print('ERROR - CONTINUE:{}'.format(e))
                continue
        #Check for rows - if none then return
        if len(_tick_df) == 0:
            return _tick_df
        #Reformat
        def float_format(_str_in):
            if type(_str_in) == str:
                _str_in = _str_in.strip()
                _str_in = re.sub('[^0-9.]','',_str_in)
                if _str_in == '':
                    _str_in = 0
                return _str_in
            else:
                return _str_in
        _tick_df.loc[:,'open'] = _tick_df.loc[:,'open'].apply(float_format).astype(float)
        _tick_df.loc[:,'high'] = _tick_df.loc[:,'high'].apply(float_format).astype(float)
        _tick_df.loc[:,'low'] = _tick_df.loc[:,'low'].apply(float_format).astype(float)
        _tick_df.loc[:,'close'] = _tick_df.loc[:,'close'].apply(float_format).astype(float)
        _tick_df.loc[:,'adj_close'] = _tick_df.loc[:,'adj_close'].apply(float_format).astype(float)
        _tick_df.loc[:,'volume'] = _tick_df.loc[:,'volume'].apply(float_format).astype(float)
        _tick_df.loc[:,'change'] = _tick_df.loc[:,'close'] - _tick_df.loc[:,'open']
        def conv_date(_str_in):
            if type(_str_in) == str:
                return dt.datetime.strptime(_str_in,'%b %d, %Y')
            else:
                return _str_in
        _tick_df.loc[:,'date'] = _tick_df.loc[:,'date'].apply(conv_date)
        #Add the ticker series
        _tick_df.loc[:,'ticker'] = _tick    
        _tick_df = _tick_df.loc[:,['ticker','date','open','close','high','low','change','volume']]
        #CLEANING - Remove any rows with zero volume
        _tick_df = _tick_df[_tick_df['volume'] > 0]
        #CLEANING - Copy row above where the change has been more than 90%
        _tick_df['cl_change'] = (_tick_df['close'] - _tick_df['close'].shift(1))/_tick_df['close'].shift(1)
        _check_s = _tick_df['cl_change'] < -0.9
        _tick_df.loc[_check_s,'open'] = _tick_df['open'].shift(-1).copy().loc[_check_s]
        _tick_df.loc[_check_s,'close'] = _tick_df['close'].shift(-1).copy().loc[_check_s]
        _tick_df.loc[_check_s,'high'] = _tick_df['high'].shift(-1).copy().loc[_check_s]
        _tick_df.loc[_check_s,'low'] = _tick_df['low'].shift(-1).copy().loc[_check_s]
        _tick_df.drop(columns='cl_change',inplace=True)
        return _tick_df
    except Exception as e:
        print('ERROR:{}'.format(e))
        return False

#Calc the ema and macds for the data
def calc_ema_macd(_tick_df):
    try:
        #Add in the ema and macd
        _tick_df = _tick_df.sort_values(by='date')
        _tick_df = _tick_df.reset_index(drop=True)
        _tick_df['ema12'] = calc_ema(_tick_df['close'],12)
        _tick_df['ema26'] = calc_ema(_tick_df['close'],26)
        _tick_df['macd_line'],_tick_df['signal_line'],_tick_df['macd'] = calc_macd(_tick_df['ema26'],_tick_df['ema12'],9)
        #Sort clean and export
        _tick_df = _tick_df.sort_values(by='date')
        _tick_df = _tick_df.reset_index(drop=True)
        return _tick_df
    except Exception as e:
        print('ERROR:{}'.format(e))
        return False

In [12]:
#Create a weekly table
def get_price_hist_w(_df_d):
    print('Converting daily prices to weekly prices')
    try:
        #Create a copy of the data
        _df_d = _df_d.copy()
        #Establish a week number for each date
        _df_d['isocalendar'] = [x.isocalendar()[:2] for x in _df_d['date']]
        #Get highs and lows
        _high_df = _df_d[['high','isocalendar']].groupby('isocalendar').max().reset_index()
        _low_df = _df_d[['low','isocalendar']].groupby('isocalendar').min().reset_index()
        #Get total volume for the week
        _vol_df = _df_d[['volume','isocalendar']].groupby('isocalendar').sum().reset_index()
        #Get open price
        _min_wk_day = _df_d[['date','isocalendar']].groupby('isocalendar').min().reset_index()
        _open_df = pd.merge(_df_d[['date','open']],_min_wk_day,left_on='date',right_on='date')
        #Get close price
        _max_wk_day = _df_d[['date','isocalendar']].groupby('isocalendar').max().reset_index()
        _close_df = pd.merge(_df_d[['date','close']],_max_wk_day,left_on='date',right_on='date').reset_index()
        #Form the final df
        _wk_df = pd.merge(_df_d[['ticker','isocalendar']],_min_wk_day,left_on='isocalendar',right_on='isocalendar') #date
        _wk_df = pd.merge(_wk_df,_high_df,left_on='isocalendar',right_on='isocalendar') #high
        _wk_df = pd.merge(_wk_df,_low_df,left_on='isocalendar',right_on='isocalendar') #low
        _wk_df = pd.merge(_wk_df,_vol_df,left_on='isocalendar',right_on='isocalendar') #volume
        _wk_df = pd.merge(_wk_df,_open_df[['isocalendar','open']],left_on='isocalendar',right_on='isocalendar') #open
        _wk_df = pd.merge(_wk_df,_close_df[['isocalendar','close']],left_on='isocalendar',right_on='isocalendar') #close
        _wk_df['change'] = _wk_df['close'] - _wk_df['open']
        _wk_df = _wk_df.drop_duplicates().reset_index(drop=True)
        #Get the monday of each week
        _wk_df['weekday'] = [dt.date.weekday(x) for x in _wk_df['date']]
        _wk_df['date'] = _wk_df['date'] - pd.Series([dt.timedelta(days=x) for x in _wk_df['weekday']])
        _wk_df.drop(columns=['isocalendar','weekday'],inplace=True)
        return _wk_df
    except Exception as e:
        print('ERROR:{}'.format(e))
        return False

In [13]:
#Establish the day ref of today compared to 01/01/1970
en_date = dt.date.today()
ep_date = dt.date(1970,1,1)
yrs = 20
st_date = dt.date(en_date.year - yrs,en_date.month,en_date.day)

In [14]:
#Scrape daily price data
hf_store_name_d = src_fldr_pth + r'all_hist_prices_d_TMP.h5'
hf_d = pd.HDFStore(hf_store_name_d)
group_name_d = r'daily_data'
hf_store_name_w = src_fldr_pth + r'all_hist_prices_w_TMP.h5'
hf_w = pd.HDFStore(hf_store_name_w)
group_name_w = r'weekly_data'
out_cols = ['ticker','date','open','close','high','low','change','volume']
count = 0
errors = []
run_time = process_time()
for tick in tick_ftse['ticker']:
    try:
        run_time.show_latest_lap_time()
        run_time.lap()
        count += 1
        print('\n{} RUNNING FOR: {}'.format(count,tick))
        
        #DAILY PRICES
        #Get daily price data
        tick_df = get_price_hist_d(tick,create_sec_ref_li(st_date,dt.datetime.today()+dt.timedelta(days=1))) #1 day ahead so today is included

        #Calc emas and macd
        tick_df = calc_ema_macd(tick_df)
        print('DAILY FINAL SHAPE: {}'.format(tick_df.shape))

        #Add to daily h5 file
        tick_df.to_hdf(hf_store_name_d,key=group_name_d,append=True,min_itemsize=col_lens)
        
        #WEEKLY PRICES
        #Convert to weekly prices
        df_w = get_price_hist_w(tick_df)

        #Calc emas and macd
        df_w = calc_ema_macd(df_w)
        print('WEEKLY FINAL SHAPE: {}'.format(df_w.shape))

        #Add to weekly h5 file
        df_w.to_hdf(hf_store_name_w,key=group_name_w,append=True,min_itemsize=col_lens)
    except Exception as e:
        print('ERROR:{}'.format(e))
        errors.append(e)
hf_d.close()
hf_w.close()
print('\n\n')
run_time.end()
print('\nERROR COUNT: {}'.format(len(errors)))
if len(errors) > 0:
    print('    ERRORS -> {}'.format(errors))


1 RUNNING FOR: III
_st_date: 1999-09-29 00:00:00
_en_date: 2019-09-30 21:34:20.577393
Getting DAILY prices for:III
DAILY FINAL SHAPE: (2971, 13)
Converting daily prices to weekly prices
WEEKLY FINAL SHAPE: (612, 13)
LAP 1 TIME -> 0:0:0

2 RUNNING FOR: ABF
_st_date: 1999-09-29 00:00:00
_en_date: 2019-09-30 21:35:39.309983
Getting DAILY prices for:ABF
DAILY FINAL SHAPE: (5044, 13)
Converting daily prices to weekly prices
WEEKLY FINAL SHAPE: (1044, 13)
LAP 2 TIME -> 0:1:18

3 RUNNING FOR: ADM
_st_date: 1999-09-29 00:00:00
_en_date: 2019-09-30 21:38:22.807588
Getting DAILY prices for:ADM
DAILY FINAL SHAPE: (1671, 13)
Converting daily prices to weekly prices
WEEKLY FINAL SHAPE: (352, 13)
LAP 3 TIME -> 0:2:43

4 RUNNING FOR: AAL
_st_date: 1999-09-29 00:00:00
_en_date: 2019-09-30 21:39:33.167969
Getting DAILY prices for:AAL
DAILY FINAL SHAPE: (4309, 13)
Converting daily prices to weekly prices
WEEKLY FINAL SHAPE: (1007, 13)
LAP 4 TIME -> 0:1:10

5 RUNNING FOR: ANTO
_st_date: 1999-09-29 00:00

DAILY FINAL SHAPE: (5016, 13)
Converting daily prices to weekly prices
WEEKLY FINAL SHAPE: (1044, 13)
LAP 35 TIME -> 0:1:58

36 RUNNING FOR: GLEN
_st_date: 1999-09-29 00:00:00
_en_date: 2019-09-30 22:41:42.181098
Getting DAILY prices for:GLEN
DAILY FINAL SHAPE: (2131, 13)
Converting daily prices to weekly prices
WEEKLY FINAL SHAPE: (437, 13)
LAP 36 TIME -> 0:1:29

37 RUNNING FOR: HLMA
_st_date: 1999-09-29 00:00:00
_en_date: 2019-09-30 22:43:12.790646
Getting DAILY prices for:HLMA
DAILY FINAL SHAPE: (4476, 13)
Converting daily prices to weekly prices
WEEKLY FINAL SHAPE: (1011, 13)
LAP 37 TIME -> 0:1:30

38 RUNNING FOR: HL.
_st_date: 1999-09-29 00:00:00
_en_date: 2019-09-30 22:44:58.799535
Getting DAILY prices for:HL
ERROR - CONTINUE:HTTPSConnectionPool(host='finance.yahoo.com', port=443): Max retries exceeded with url: /quote/HL.L/history?period1=1473033600&period2=1485129600&interval=1d&filter=history&frequency=1d (Caused by NewConnectionError('<urllib3.connection.VerifiedHTTPSConnecti

DAILY FINAL SHAPE: (683, 13)
Converting daily prices to weekly prices
WEEKLY FINAL SHAPE: (140, 13)
LAP 38 TIME -> 0:1:46

39 RUNNING FOR: HIK
_st_date: 1999-09-29 00:00:00
_en_date: 2019-09-30 22:47:58.914842
Getting DAILY prices for:HIK
ERROR - CONTINUE:HTTPSConnectionPool(host='finance.yahoo.com', port=443): Max retries exceeded with url: /quote/HIK.L/history?period1=1557705600&period2=1569801600&interval=1d&filter=history&frequency=1d (Caused by NewConnectionError('<urllib3.connection.VerifiedHTTPSConnection object at 0x000001F3D6F35780>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
ERROR - CONTINUE:HTTPSConnectionPool(host='finance.yahoo.com', port=443): Max retries exceeded with url: /quote/HIK.L/history?period1=1545609600&period2=1557705600&interval=1d&filter=history&frequency=1d (Caused by NewConnectionError('<urllib3.connection.VerifiedHTTPSConnection object at 0x000001F3D6F35400>: Failed to establish a new connection: [Errno 11001] getaddrinfo fai

ERROR - CONTINUE:HTTPSConnectionPool(host='finance.yahoo.com', port=443): Max retries exceeded with url: /quote/HSX.L/history?period1=1460937600&period2=1473033600&interval=1d&filter=history&frequency=1d (Caused by NewConnectionError('<urllib3.connection.VerifiedHTTPSConnection object at 0x000001F3D6F35400>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
ERROR - CONTINUE:HTTPSConnectionPool(host='finance.yahoo.com', port=443): Max retries exceeded with url: /quote/HSX.L/history?period1=1448841600&period2=1460937600&interval=1d&filter=history&frequency=1d (Caused by NewConnectionError('<urllib3.connection.VerifiedHTTPSConnection object at 0x000001F3D6F35AC8>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
ERROR - CONTINUE:HTTPSConnectionPool(host='finance.yahoo.com', port=443): Max retries exceeded with url: /quote/HSX.L/history?period1=1436745600&period2=1448841600&interval=1d&filter=history&frequency=1d (Caused by NewConnectionErro

ERROR - CONTINUE:HTTPSConnectionPool(host='finance.yahoo.com', port=443): Max retries exceeded with url: /quote/HSBA.L/history?period1=1315785600&period2=1327881600&interval=1d&filter=history&frequency=1d (Caused by NewConnectionError('<urllib3.connection.VerifiedHTTPSConnection object at 0x000001F3D6F35208>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
ERROR - CONTINUE:HTTPSConnectionPool(host='finance.yahoo.com', port=443): Max retries exceeded with url: /quote/HSBA.L/history?period1=1303689600&period2=1315785600&interval=1d&filter=history&frequency=1d (Caused by NewConnectionError('<urllib3.connection.VerifiedHTTPSConnection object at 0x000001F3D6F359B0>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
ERROR - CONTINUE:HTTPSConnectionPool(host='finance.yahoo.com', port=443): Max retries exceeded with url: /quote/HSBA.L/history?period1=1291593600&period2=1303689600&interval=1d&filter=history&frequency=1d (Caused by NewConnectionE

...

ERROR - CONTINUE:HTTPSConnectionPool(host='finance.yahoo.com', port=443): Max retries exceeded with url: /quote/WMH.L/history?period1=1098144000&period2=1110240000&interval=1d&filter=history&frequency=1d (Caused by NewConnectionError('<urllib3.connection.VerifiedHTTPSConnection object at 0x000001F3D78ACB00>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
ERROR - CONTINUE:HTTPSConnectionPool(host='finance.yahoo.com', port=443): Max retries exceeded with url: /quote/WMH.L/history?period1=1086048000&period2=1098144000&interval=1d&filter=history&frequency=1d (Caused by NewConnectionError('<urllib3.connection.VerifiedHTTPSConnection object at 0x000001F3D78AC208>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
ERROR - CONTINUE:HTTPSConnectionPool(host='finance.yahoo.com', port=443): Max retries exceeded with url: /quote/WMH.L/history?period1=1073952000&period2=1086048000&interval=1d&filter=history&frequency=1d (Caused by NewConnectionErro

ERROR - CONTINUE:HTTPSConnectionPool(host='finance.yahoo.com', port=443): Max retries exceeded with url: /quote/WTAN.L/history?period1=1001376000&period2=1013472000&interval=1d&filter=history&frequency=1d (Caused by NewConnectionError('<urllib3.connection.VerifiedHTTPSConnection object at 0x000001F3D78AC278>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
ERROR - CONTINUE:HTTPSConnectionPool(host='finance.yahoo.com', port=443): Max retries exceeded with url: /quote/WTAN.L/history?period1=989280000&period2=1001376000&interval=1d&filter=history&frequency=1d (Caused by NewConnectionError('<urllib3.connection.VerifiedHTTPSConnection object at 0x000001F3D78AC1D0>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
ERROR - CONTINUE:HTTPSConnectionPool(host='finance.yahoo.com', port=443): Max retries exceeded with url: /quote/WTAN.L/history?period1=977184000&period2=989280000&interval=1d&filter=history&frequency=1d (Caused by NewConnectionErro

ERROR - CONTINUE:HTTPSConnectionPool(host='finance.yahoo.com', port=443): Max retries exceeded with url: /quote/WIZZ.L/history?period1=952992000&period2=965088000&interval=1d&filter=history&frequency=1d (Caused by NewConnectionError('<urllib3.connection.VerifiedHTTPSConnection object at 0x000001F3D78AC208>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
ERROR - CONTINUE:HTTPSConnectionPool(host='finance.yahoo.com', port=443): Max retries exceeded with url: /quote/WIZZ.L/history?period1=940896000&period2=952992000&interval=1d&filter=history&frequency=1d (Caused by NewConnectionError('<urllib3.connection.VerifiedHTTPSConnection object at 0x000001F3D78ACBE0>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
ERROR - CONTINUE:HTTPSConnectionPool(host='finance.yahoo.com', port=443): Max retries exceeded with url: /quote/WIZZ.L/history?period1=938563200&period2=940896000&interval=1d&filter=history&frequency=1d (Caused by NewConnectionError('

ERROR - CONTINUE:HTTPSConnectionPool(host='finance.yahoo.com', port=443): Max retries exceeded with url: /quote/WKP.L/history?period1=1509408000&period2=1521504000&interval=1d&filter=history&frequency=1d (Caused by NewConnectionError('<urllib3.connection.VerifiedHTTPSConnection object at 0x000001F3D78AC278>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
ERROR - CONTINUE:HTTPSConnectionPool(host='finance.yahoo.com', port=443): Max retries exceeded with url: /quote/WKP.L/history?period1=1497312000&period2=1509408000&interval=1d&filter=history&frequency=1d (Caused by NewConnectionError('<urllib3.connection.VerifiedHTTPSConnection object at 0x000001F3D78AC198>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
ERROR - CONTINUE:HTTPSConnectionPool(host='finance.yahoo.com', port=443): Max retries exceeded with url: /quote/WKP.L/history?period1=1485216000&period2=1497312000&interval=1d&filter=history&frequency=1d (Caused by NewConnectionErro

ERROR - CONTINUE:HTTPSConnectionPool(host='finance.yahoo.com', port=443): Max retries exceeded with url: /quote/WWH.L/history?period1=1388448000&period2=1400544000&interval=1d&filter=history&frequency=1d (Caused by NewConnectionError('<urllib3.connection.VerifiedHTTPSConnection object at 0x000001F3D78ACF98>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
ERROR - CONTINUE:HTTPSConnectionPool(host='finance.yahoo.com', port=443): Max retries exceeded with url: /quote/WWH.L/history?period1=1376352000&period2=1388448000&interval=1d&filter=history&frequency=1d (Caused by NewConnectionError('<urllib3.connection.VerifiedHTTPSConnection object at 0x000001F3D78AC128>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))
ERROR - CONTINUE:HTTPSConnectionPool(host='finance.yahoo.com', port=443): Max retries exceeded with url: /quote/WWH.L/history?period1=1364256000&period2=1376352000&interval=1d&filter=history&frequency=1d (Caused by NewConnectionErro

In [15]:
#close any open h5 files
tables.file._open_files.close_all()

In [16]:
#Delete the old h5 file and rename the TMP
try:
    os.remove(src_fldr_pth + r'all_hist_prices_d.h5')
    print('\nSUCCESSFULLY REMOVED {}'.format(src_fldr_pth + r'all_hist_prices_d.h5'))
except Exception as e:
    print('\nERROR - REMOVING:{}'.format(e))
try:
    os.rename(src_fldr_pth + r'all_hist_prices_d_TMP.h5',src_fldr_pth + r'all_hist_prices_d.h5')
    print('\nSUCCESSFULLY RENAMED {} TO {}'.format(src_fldr_pth + r'all_hist_prices_d_TMP.h5',src_fldr_pth + r'all_hist_prices_d.h5'))
except Exception as e:
    print('\nERROR - RENAMING:{}'.format(e))


SUCCESSFULLY REMOVED C:\\Users\\Robert\\Documents\\python_scripts\\stock_trading_ml_modelling\\historical_prices\\all_hist_prices_d.h5

SUCCESSFULLY RENAMED C:\\Users\\Robert\\Documents\\python_scripts\\stock_trading_ml_modelling\\historical_prices\\all_hist_prices_d_TMP.h5 TO C:\\Users\\Robert\\Documents\\python_scripts\\stock_trading_ml_modelling\\historical_prices\\all_hist_prices_d.h5


In [17]:
#Delete the old h5 file and rename the TMP
try:
    os.remove(src_fldr_pth + r'all_hist_prices_w.h5')
    print('\nSUCCESSFULLY REMOVED {}'.format(src_fldr_pth + r'all_hist_prices_w.h5'))
except Exception as e:
    print('\nERROR - REMOVING:{}'.format(e))
try:
    os.rename(src_fldr_pth + r'all_hist_prices_w_TMP.h5',src_fldr_pth + r'all_hist_prices_w.h5')
    print('\nSUCCESSFULLY RENAMED {} TO {}'.format(src_fldr_pth + r'all_hist_prices_w_TMP.h5',src_fldr_pth + r'all_hist_prices_w.h5'))
except Exception as e:
    print('\nERROR - RENAMING:{}'.format(e))


SUCCESSFULLY REMOVED C:\\Users\\Robert\\Documents\\python_scripts\\stock_trading_ml_modelling\\historical_prices\\all_hist_prices_w.h5

SUCCESSFULLY RENAMED C:\\Users\\Robert\\Documents\\python_scripts\\stock_trading_ml_modelling\\historical_prices\\all_hist_prices_w_TMP.h5 TO C:\\Users\\Robert\\Documents\\python_scripts\\stock_trading_ml_modelling\\historical_prices\\all_hist_prices_w.h5


# Exporting the FTSE ticker list

In [18]:
#Export the ftse list
path = "C:\\Users\\Robert\\Documents\\python_scripts\\stock_trading_ml_modelling\\historical_prices\\"
tick_ftse.to_csv(path_or_buf=path + "tick_ftse.csv")

In [19]:
#End the program
import sys
sys.exit()

SystemExit: 

C:\Users\Robert\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:2969: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
